# Segmenting and Clustering Neighborhoods in Toronto

## Downloading all needed dependencies

In [11]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


## Scraping the postal codes of Canada

In [1]:
import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_db5025c900644ceb8b47568c9f8c57ff = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='EdIWvgkEmchshmnNVcpOpwPunP3NoqBEGbGITCzc9nQL',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_db5025c900644ceb8b47568c9f8c57ff.get_object(Bucket='courseracapstone-donotdelete-pr-axwptsovobk1xb',Key='PostalCodesCA.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_8 = pd.read_csv(body)
df_data_8.head()

Postal Code          Borough                      Neighbourhood
0         M4N  Central Toronto                      Lawrence Park
1         M4P  Central Toronto                   Davisville North
2         M4R  Central Toronto  North Toronto West- Lawrence Park
3         M4S  Central Toronto                         Davisville
4         M4T  Central Toronto        Moore Park- Summerhill East

In [2]:
# Creating dataframe with sorted values by respective postal codes
pcodesca=df_data_8.sort_values(by=['Postal Code'])
pcodesca.head()

Postal Code      Borough                           Neighbourhood
75         M1B  Scarborough                          Malvern- Rouge
76         M1C  Scarborough  Rouge Hill- Port Union- Highland Creek
77         M1E  Scarborough       Guildwood- Morningside- West Hill
78         M1G  Scarborough                                  Woburn
79         M1H  Scarborough                               Cedarbrae

In [3]:
pcodesca.shape

(103, 3)

## Reading longitudes and latitudes 

In [4]:
body = client_db5025c900644ceb8b47568c9f8c57ff.get_object(Bucket='courseracapstone-donotdelete-pr-axwptsovobk1xb',Key='Geospatial_Coordinates.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_7 = pd.read_csv(body)
df_data_7.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [5]:
latlon1=df_data_7
latlon1.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [6]:
# Creating dataframe with sorted values by respective postal codes
latlon=latlon1.sort_values(by=['Postal Code'])
latlon.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [7]:
latlon.shape

(103, 3)

## Appending latidues and longitudes to each postal code

In [8]:
pcodesca['Latitude']=pd.Series(latlon['Latitude'])
pcodesca['Longitude']=pd.Series(latlon['Longitude'])
pcodesca.head()

Postal Code      Borough                           Neighbourhood  \
75         M1B  Scarborough                          Malvern- Rouge   
76         M1C  Scarborough  Rouge Hill- Port Union- Highland Creek   
77         M1E  Scarborough       Guildwood- Morningside- West Hill   
78         M1G  Scarborough                                  Woburn   
79         M1H  Scarborough                               Cedarbrae   

     Latitude  Longitude  
75  43.669542 -79.422564  
76  43.669005 -79.442259  
77  43.647927 -79.419750  
78  43.636847 -79.428191  
79  43.713756 -79.490074

## Creating new dataframe with complete data

In [9]:
PostalCodes=pcodesca.reset_index(drop=True)
PostalCodes.head()

Postal Code      Borough                           Neighbourhood   Latitude  \
0         M1B  Scarborough                          Malvern- Rouge  43.669542   
1         M1C  Scarborough  Rouge Hill- Port Union- Highland Creek  43.669005   
2         M1E  Scarborough       Guildwood- Morningside- West Hill  43.647927   
3         M1G  Scarborough                                  Woburn  43.636847   
4         M1H  Scarborough                               Cedarbrae  43.713756   

   Longitude  
0 -79.422564  
1 -79.442259  
2 -79.419750  
3 -79.428191  
4 -79.490074

## Use geopy library to get the latitude and longitude values of Toronto, CA.

In [12]:
address = 'Toronto, CA'

geolocator = Nominatim(user_agent="CA_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto, CA are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto, CA are 43.6534817, -79.3839347.


## Create a map of Toronto, CA with neighborhoods superimposed on top.

In [13]:
# create map of Toronto, CA using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(PostalCodes['Latitude'], PostalCodes['Longitude'], PostalCodes['Borough'], PostalCodes['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

## Define Foursquare Credentials and Version

In [55]:
CLIENT_ID = 'UVSCUVVCDCWMZPK1XMQQK5XAWAL5BAHH3UXSHYSMEG0A1HYF' # your Foursquare ID
CLIENT_SECRET = 'JG11LJH3TZD15NLIQKRTG2CCGYIPNHNV1FH4OTMHCIBBYM1B' # your Foursquare Secret
VERSION = '20200801' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: UVSCUVVCDCWMZPK1XMQQK5XAWAL5BAHH3UXSHYSMEG0A1HYF
CLIENT_SECRET:JG11LJH3TZD15NLIQKRTG2CCGYIPNHNV1FH4OTMHCIBBYM1B


In [58]:
PostalCodes.loc[21, 'Neighbourhood']

'Willowdale- Newtonbrook'

In [59]:
neighborhood_latitude = PostalCodes.loc[21, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = PostalCodes.loc[21, 'Longitude'] # neighborhood longitude value

neighborhood_name = PostalCodes.loc[21, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Willowdale- Newtonbrook are 43.6514939, -79.3754179.


In [67]:
# type your answer here

LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=UVSCUVVCDCWMZPK1XMQQK5XAWAL5BAHH3UXSHYSMEG0A1HYF&client_secret=JG11LJH3TZD15NLIQKRTG2CCGYIPNHNV1FH4OTMHCIBBYM1B&v=20200801&ll=43.6514939,-79.3754179&radius=500&limit=100'

In [68]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f384aadacc11570be0c5547'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'St. Lawrence',
  'headerFullLocation': 'St. Lawrence, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 85,
  'suggestedBounds': {'ne': {'lat': 43.6559939045, 'lng': -79.36921018606671},
   'sw': {'lat': 43.646993895499996, 'lng': -79.3816256139333}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4af618daf964a520220122e3',
       'name': 'GEORGE Restaurant',
       'location': {'address': '111c Queen St East',
        'crossStreet': 'Church',
        'lat': 43.65334645635036,
        'lng': -79.3744449051126,
        'labeledLatLngs': [{'label'

In [69]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [70]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name           categories        lat  \
0                          GEORGE Restaurant           Restaurant  43.653346   
1                      Gyu-Kaku Japanese BBQ  Japanese Restaurant  43.651422   
2                                    Terroni   Italian Restaurant  43.650927   
3  GoodLife Fitness Toronto 137 Yonge Street                  Gym  43.651242   
4                          Fahrenheit Coffee          Coffee Shop  43.652384   

         lng  
0 -79.374445  
1 -79.375047  
2 -79.375602  
3 -79.378068  
4 -79.372719

In [71]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

85 venues were returned by Foursquare.


In [72]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [76]:
Wenk_venues = getNearbyVenues(names=PostalCodes['Neighbourhood'],
                                   latitudes=PostalCodes['Latitude'],
                                   longitudes=PostalCodes['Longitude']
                                  )

Malvern- Rouge
Rouge Hill- Port Union- Highland Creek
Guildwood- Morningside- West Hill
Woburn
Cedarbrae
Scarborough Village
Kennedy Park- Ionview- East Birchmount Park
Golden Mile- Clairlea- Oakridge
Cliffside- Cliffcrest- Scarborough Village West
Birch Cliff- Cliffside West
Dorset Park- Wexford Heights- Scarborough Town Centre
Wexford- Maryvale
Agincourt
Clarks Corners- Tam O'Shanter- Sullivan
Milliken- Agincourt North- Steeles East- L'Amoreaux East
Steeles West- L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview- Henry Farm- Oriole
Bayview Village
York Mills- Silver Hills
Willowdale- Newtonbrook
Willowdale- Willowdale East
York Mills West
Willowdale- Willowdale West
Parkwoods
Don Mills
Don Mills
Bathurst Manor- Wilson Heights- Downsview North
Northwood Park- York University
Downsview
Downsview
Downsview
Downsview
Victoria Village
Parkview Hill- Woodbine Gardens
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto- Broadview North (Old East York)
The Danforth West- 

In [77]:
print(Wenk_venues.shape)
Wenk_venues.head()

(2124, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Malvern- Rouge              43.669542              -79.422564   
1  Malvern- Rouge              43.669542              -79.422564   
2  Malvern- Rouge              43.669542              -79.422564   
3  Malvern- Rouge              43.669542              -79.422564   
4  Malvern- Rouge              43.669542              -79.422564   

                  Venue  Venue Latitude  Venue Longitude      Venue Category  
0          Fiesta Farms       43.668471       -79.420485       Grocery Store  
1           Contra Cafe       43.669107       -79.426105                Café  
2             Starbucks       43.671530       -79.421400         Coffee Shop  
3        Vinny’s Panini       43.670679       -79.426148  Italian Restaurant  
4  Scout and Cash Caffe       43.667360       -79.419938                Café

In [78]:
Wenk_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                              14   
Alderwood- Long Branch                                                 20   
Bathurst Manor- Wilson Heights- Downsview North                        25   
Bayview Village                                                        45   
Bedford Park- Lawrence Manor East                                      96   
Berczy Park                                                            13   
Birch Cliff- Cliffside West                                            35   
Business reply mail Processing Centre- South Ce...                      4   
CN Tower- King and Spadina- Railway Lands- Harb...                      2   
Caledonia-Fairbanks                                                     8   
Canada Post Gateway Processing Centre                                   4   
Cedarbrae                                                               5   
Christie                                                                4   
Church and Wellesley                                                    6   
Clarks Corners- Tam O'Shanter- Sullivan                                13   
Cliffside- Cliffcrest- Scarborough Village West                        14   
Davisville                                                              3   
Davisville North                                                        2   
Del Ray- Mount Dennis- Keelsdale and Silverthorn                        4   
Don Mills                                                             200   
Dorset Park- Wexford Heights- Scarborough Town ...                     36   
Downsview                                                             124   
Dufferin- Dovercourt Village                                           15   
East Toronto- Broadview North (Old East York)                           4   
Eringate- Bloordale Gardens- Old Burnhamthorpe-...                      8   
Fairview- Henry Farm- Oriole                                           74   
First Canadian Place- Underground city                                  2   
Forest Hill North & West- Forest Hill Road Park                        10   
Garden District- Ryerson                                               14   
Glencairn                                                              12   
Golden Mile- Clairlea- Oakridge                                        24   
Guildwood- Morningside- West Hill                                      47   
Harbourfront East- Union Station- Toronto Islands                      62   
High Park- The Junction South                                           9   
Hillcrest Village                                                      42   
Humber Summit                                                           4   
Humberlea- Emery                                                        4   
Humewood-Cedarvale                                                      1   
India Bazaar- The Beaches West                                          2   
Islington Avenue- Humber Valley Village                                40   
Kennedy Park- Ionview- East Birchmount Park                             4   
Kensington Market- Chinatown- Grange Park                              34   
Kingsview Village- St. Phillips- Martin Grove G...                     35   
Lawrence Manor- Lawrence Heights                                      100   
Lawrence Park                                                           1   
Leaside                                                                10   
Malvern- Rouge                                                         17   
Milliken- Agincourt North- Steeles East- L'Amor...                      6   
Mimico NW- The Queensway West- South of Bloor- ...                     19   
Moore Park- Summerhill East                                             8   
New Toronto- Mimico South- Humber Bay Shores    

In [79]:
print('There are {} uniques categories.'.format(len(Wenk_venues['Venue Category'].unique())))

There are 269 uniques categories.


In [80]:
# one hot encoding
Wenk_onehot = pd.get_dummies(Wenk_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Wenk_onehot['Neighborhood'] = Wenk_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Wenk_onehot.columns[-1]] + list(Wenk_onehot.columns[:-1])
Wenk_onehot = Wenk_onehot[fixed_columns]

Wenk_onehot.head()


Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0            0          0           0           0       0     0    0   
1            0          0           0           0       0     0    0   
2            0          0           0           0       0     0    0   
3            0          0           0           0       0     0    0   
4            0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Rental / Bike Share  Bike Shop  Bistro  Boat or Ferry  Bookstore  \
0                         0          0       0              0          0   
1                         0          0       0              0          0   
2                         0          0       0              0          0   
3                         0          0       0              0          0   
4                         0          0       0              0          0   

   Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0         0                     0               0        0            0   
1         0                     0               0        0            0   
2         0                     0               0        0            0   
3         0                     0               0        0            0   
4         0                     0               0        0            0   

   B

In [81]:
Wenk_onehot.shape

(2124, 269)

In [82]:
Wenk_grouped = Wenk_onehot.groupby('Neighborhood').mean().reset_index()
Wenk_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood- Long Branch     0.050000   
2     Bathurst Manor- Wilson Heights- Downsview North     0.000000   
3                                     Bayview Village     0.022222   
4                   Bedford Park- Lawrence Manor East     0.010417   
5                                         Berczy Park     0.000000   
6                         Birch Cliff- Cliffside West     0.028571   
7   Business reply mail Processing Centre- South C...     0.000000   
8   CN Tower- King and Spadina- Railway Lands- Har...     0.000000   
9                                 Caledonia-Fairbanks     0.000000   
10              Canada Post Gateway Processing Centre     0.000000   
11                                          Cedarbrae     0.000000   
12                                           Christie     0.000000   
13                               Church and Wellesley     0.000000   
14            Clarks Corners- Tam O'Shanter- Sullivan     0.000000   
15    Cliffside- Cliffcrest- Scarborough Village West     0.000000   
16                                         Davisville     0.000000   
17                                   Davisville North     0.000000   
18   Del Ray- Mount Dennis- Keelsdale and Silverthorn     0.000000   
19                                          Don Mills     0.000000   
20  Dorset Park- Wexford Heights- Scarborough Town...     0.027778   
21                                          Downsview     0.008065   
22                       Dufferin- Dovercourt Village     0.000000   
23      East Toronto- Broadview North (Old East York)     0.000000   
24  Eringate- Bloordale Gardens- Old Burnhamthorpe...     0.000000   
25                       Fairview- Henry Farm- Oriole     0.027027   
26             First Canadian Place- Underground city     0.000000   
27    Forest Hill North & West- Forest Hill Road Park     0.000000   
28                           Garden District- Ryerson     0.000000   
29                                          Glencairn     0.000000   
30                    Golden Mile- Clairlea- Oakridge     0.000000   
31                  Guildwood- Morningside- West Hill     0.021277   
32  Harbourfront East- Union Station- Toronto Islands     0.000000   
33                      High Park- The Junction South     0.000000   
34                                  Hillcrest Village     0.000000   
35                                      Humber Summit     0.000000   
36                                   Humberlea- Emery     0.000000   
37                                 Humewood-Cedarvale     0.000000   
38                     India Bazaar- The Beaches West     0.000000   
39            Islington Avenue- Humber Valley Village     0.025000   
40        Kennedy Park- Ionview- East Birchmount Park     0.000000   
41          Kensington Market- Chinatown- Grange Park     0.000000   
42  Kingsview Village- St. Phillips- Martin Grove ...     0.000000   
43                   Lawrence Manor- Lawrence Heights     0.000000   
44                                      Lawrence Park     0.000000   
45                                            Leaside     0.000000   
46                                     Malvern- Rouge     0.000000   
47  Milliken- Agincourt North- Steeles East- L'Amo...     0.000000   
48  Mimico NW- The Queensway West- South of Bloor-...     0.000000   
49                        Moore Park- Summerhill East     0.000000   
50       New Toronto- Mimico South- Humber Bay Shores     0.000000   
51           North Park- Maple Leaf Park- Upwood Park     0.000000   
52                  North Toronto West- Lawrence Park     0.000000   
53                Northwest- West Humber - Clairville     0.000000   
54                    Northwood Park- York University     0.000000   
55  Old Mill South- King's Mill Park- Sunnylea- Hu...     0.023810   
56                             Parkdale- Roncesvall

In [83]:
Wenk_grouped.shape

(95, 269)

In [84]:
num_top_venues = 5

for hood in Wenk_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Wenk_grouped[Wenk_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                  venue  freq
0    Light Rail Station  0.14
1                  Park  0.07
2            Restaurant  0.07
3  Fast Food Restaurant  0.07
4            Comic Shop  0.07


----Alderwood- Long Branch----
               venue  freq
0  Indian Restaurant  0.10
1     Sandwich Place  0.10
2        Yoga Studio  0.05
3               Bank  0.05
4                Gym  0.05


----Bathurst Manor- Wilson Heights- Downsview North----
                venue  freq
0      Sandwich Place  0.08
1          Restaurant  0.08
2  Italian Restaurant  0.08
3         Coffee Shop  0.08
4    Toy / Game Store  0.04


----Bayview Village----
         venue  freq
0  Coffee Shop  0.18
1       Bakery  0.07
2         Café  0.07
3          Pub  0.07
4         Park  0.07


----Bedford Park- Lawrence Manor East----
         venue  freq
0  Coffee Shop  0.10
1         Café  0.04
2   Restaurant  0.03
3          Pub  0.03
4     Beer Bar  0.03


----Berczy Park----
                  venue  freq
0      

         venue  freq
0         Café  0.10
1  Coffee Shop  0.08
2      Brewery  0.05
3       Bakery  0.05
4    Gastropub  0.05


----Kennedy Park- Ionview- East Birchmount Park----
                venue  freq
0         Pizza Place  0.25
1       Grocery Store  0.25
2            Bus Line  0.25
3             Brewery  0.25
4  Mexican Restaurant  0.00


----Kensington Market- Chinatown- Grange Park----
              venue  freq
0  Ramen Restaurant  0.09
1       Coffee Shop  0.06
2    Sandwich Place  0.06
3              Café  0.06
4        Restaurant  0.06


----Kingsview Village- St. Phillips- Martin Grove Gardens- Richview Gardens----
              venue  freq
0       Pizza Place  0.11
1      Dessert Shop  0.09
2    Sandwich Place  0.09
3               Gym  0.06
4  Sushi Restaurant  0.06


----Lawrence Manor- Lawrence Heights----
                 venue  freq
0          Coffee Shop  0.13
1                 Café  0.07
2                Hotel  0.05
3                  Gym  0.04
4  Japanese Restau

                    venue  freq
0  Furniture / Home Store  0.17
1          Massage Studio  0.17
2    Caribbean Restaurant  0.17
3             Coffee Shop  0.17
4                     Bar  0.17


----The Kingsway- Montgomery Road- Old Mill North----
                venue  freq
0        Intersection  0.25
1                Park  0.25
2         Coffee Shop  0.25
3   Convenience Store  0.25
4  Mexican Restaurant  0.00


----Thorncliffe Park----
                venue  freq
0        Skating Rink  0.33
1                Park  0.17
2  Athletics & Sports  0.17
3          Beer Store  0.17
4         Curling Ice  0.17


----Toronto Dominion Centre- Design Exchange----
                 venue  freq
0                 Café  0.25
1                 Bank  0.25
2  Japanese Restaurant  0.25
3   Chinese Restaurant  0.25
4          Yoga Studio  0.00


----University of Toronto- Harbord----
                        venue  freq
0                        Park   1.0
1                 Yoga Studio   0.0
2              

In [85]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [86]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Wenk_grouped['Neighborhood']

for ind in np.arange(Wenk_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Wenk_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt    Light Rail Station   
1                           Alderwood- Long Branch     Indian Restaurant   
2  Bathurst Manor- Wilson Heights- Downsview North            Restaurant   
3                                  Bayview Village           Coffee Shop   
4                Bedford Park- Lawrence Manor East           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                Garden                  Park           Pizza Place   
1        Sandwich Place           Yoga Studio           Supermarket   
2        Sandwich Place           Coffee Shop    Italian Restaurant   
3                Bakery                   Pub                  Café   
4                  Café            Restaurant                   Gym   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Comic Shop            Restaurant         Burrito Place   
1         Grocery Store                   Gym           Gas Station   
2        Breakfast Spot     Indian Restaurant               Butcher   
3                  Park               Theater        Breakfast Spot   
4   Japanese Restaurant    Italian Restaurant              Beer Bar   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0               Brewery            Skate Park         Farmers Market  
1  Fast Food Restaurant          Liquor Store         Discount Store  
2                  Café      Sushi Restaurant           Cupcake Shop  
3           Event Space            Restaurant  Performing Arts Venue  
4                 Hotel                   Pub     Seafood Restaurant

In [87]:
# set number of clusters
kclusters = 5

Wenk_grouped_clustering = Wenk_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Wenk_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 1, 1, 1, 2, 1], dtype=int32)

In [88]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Wenk_merged = Wenk

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
Wenk_merged = Wenk_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

Wenk_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Malvern- Rouge              43.669542              -79.422564   
1  Malvern- Rouge              43.669542              -79.422564   
2  Malvern- Rouge              43.669542              -79.422564   
3  Malvern- Rouge              43.669542              -79.422564   
4  Malvern- Rouge              43.669542              -79.422564   

                  Venue  Venue Latitude  Venue Longitude      Venue Category  \
0          Fiesta Farms       43.668471       -79.420485       Grocery Store   
1           Contra Cafe       43.669107       -79.426105                Café   
2             Starbucks       43.671530       -79.421400         Coffee Shop   
3        Vinny’s Panini       43.670679       -79.426148  Italian Restaurant   
4  Scout and Cash Caffe       43.667360       -79.419938                Café   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               1         Grocery Store                  Café   
1               1         Grocery Store                  Café   
2               1         Grocery Store                  Café   
3               1         Grocery Store                  Café   
4               1         Grocery Store                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Park            Restaurant                 Diner   
1                  Park            Restaurant                 Diner   
2                  Park            Restaurant                 Diner   
3                  Park            Restaurant                 Diner   
4                  Park            Restaurant                 Diner   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Baby Store             Nightclub           Coffee Shop   
1            Baby Store             Nightclub           Coffee Shop   
2            Baby Store             Nightclub           Coffee Shop   
3            Baby Store             Nightclub           Coffee Shop   
4            Baby Store             Nightclub           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
0    Athletics & Sports            Candy Store  
1    Athletics & Sports            Candy Store  
2    Athletics & Sports            Candy Store  
3    Athletics & Sports            Candy Store  
4    Athletics & Sports            Candy Store

In [95]:
Wenk_merged.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Malvern- Rouge              43.669542              -79.422564   
1  Malvern- Rouge              43.669542              -79.422564   
2  Malvern- Rouge              43.669542              -79.422564   
3  Malvern- Rouge              43.669542              -79.422564   
4  Malvern- Rouge              43.669542              -79.422564   

                  Venue  Venue Latitude  Venue Longitude      Venue Category  \
0          Fiesta Farms       43.668471       -79.420485       Grocery Store   
1           Contra Cafe       43.669107       -79.426105                Café   
2             Starbucks       43.671530       -79.421400         Coffee Shop   
3        Vinny’s Panini       43.670679       -79.426148  Italian Restaurant   
4  Scout and Cash Caffe       43.667360       -79.419938                Café   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               1         Grocery Store                  Café   
1               1         Grocery Store                  Café   
2               1         Grocery Store                  Café   
3               1         Grocery Store                  Café   
4               1         Grocery Store                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Park            Restaurant                 Diner   
1                  Park            Restaurant                 Diner   
2                  Park            Restaurant                 Diner   
3                  Park            Restaurant                 Diner   
4                  Park            Restaurant                 Diner   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Baby Store             Nightclub           Coffee Shop   
1            Baby Store             Nightclub           Coffee Shop   
2            Baby Store             Nightclub           Coffee Shop   
3            Baby Store             Nightclub           Coffee Shop   
4            Baby Store             Nightclub           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
0    Athletics & Sports            Candy Store  
1    Athletics & Sports            Candy Store  
2    Athletics & Sports            Candy Store  
3    Athletics & Sports            Candy Store  
4    Athletics & Sports            Candy Store

In [99]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Wenk_merged['Neighborhood Latitude'], Wenk_merged['Neighborhood Longitude'], Wenk_merged['Neighborhood'], Wenk_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster -1],
        fill=True,
        fill_color=rainbow[cluster -1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters